In [1]:
# 라이브러리 import
!pip install pandas-profiling[notebook]
import requests
import json
import pandas as pd
import numpy as np
from pandas_profiling import ProfileReport

C:\Users\USER\AppData\Local\Temp\ipykernel_10076\1885267715.py:7: DeprecationWarning: `import pandas_profiling` is going to be deprecated by April 1st. Please use `import ydata_profiling` instead.
  from pandas_profiling import ProfileReport


In [2]:
#id정보 불러오기
url_id = 'http://www.smartfarmkorea.net/Agree_WS/webservices/ProvideRestService/getIdentityDataList/fc918c3668964be490f67fe52bbef49c'
response = requests.get(url_id)
contents = response.text
js = json.loads(contents)

In [3]:
js = json.loads(contents)
print(type(js)) #json타입 확인

<class 'list'>


In [4]:
#df으로
js = json.loads(contents)
df_id = pd.DataFrame(js)
df_id

statusCode statusMessage    userId   facilityId  addressName itemCode
0           00   NORMAL_CODE  LSDS_001  LSDS_001_01     경상남도 하동군   413000
1         None          None  LSDS_002  LSDS_002_01     충청남도 천안시   413000
2         None          None  LSDS_003  LSDS_003_01     충청남도 천안시   413000
3         None          None  LSDS_005  LSDS_005_01      경기도 여주군   413000
4         None          None  LSDS_006  LSDS_006_01     경상북도 포항시   413000
..         ...           ...       ...          ...          ...      ...
888       None          None    sk0081    sk0081_01  세종특별자치시 연동면   080300
889       None          None    sk0085    sk0085_01  세종특별자치시 연동면   080300
890       None          None    sk0091    sk0091_01  세종특별자치시 연동면   080300
891       None          None    sk0104    sk0104_01  세종특별자치시 연동면   080300
892       None          None    sk0118    sk0118_01  세종특별자치시 연동면   080300

[893 rows x 6 columns]

In [5]:
#fast EDA
profile = ProfileReport(df_id, title="Report")
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

ID set
- 총 892농가
- userid facilityId 1:1매칭 
- addressname 결측값 86개 
- itmecode 토마토(080300):151농가, 딸기(080400):293농가, 방토(080600):1농가 

In [22]:
# df_item_list=['080400'] #딸기 농가만 남기기 294농가
# raw_id=df_id[df_id['itemCode'].isin(df_item_list)]
# print(len(df_id[(df_id['itemCode'].isin(df_item_list))&(df_id['addressName']=='null')])) #딸기 농가중엔 지역코드 결측 없음

raw_id=df_id
raw_id

statusCode statusMessage    userId   facilityId  addressName itemCode
0           00   NORMAL_CODE  LSDS_001  LSDS_001_01     경상남도 하동군   413000
1         None          None  LSDS_002  LSDS_002_01     충청남도 천안시   413000
2         None          None  LSDS_003  LSDS_003_01     충청남도 천안시   413000
3         None          None  LSDS_005  LSDS_005_01      경기도 여주군   413000
4         None          None  LSDS_006  LSDS_006_01     경상북도 포항시   413000
..         ...           ...       ...          ...          ...      ...
888       None          None    sk0081    sk0081_01  세종특별자치시 연동면   080300
889       None          None    sk0085    sk0085_01  세종특별자치시 연동면   080300
890       None          None    sk0091    sk0091_01  세종특별자치시 연동면   080300
891       None          None    sk0104    sk0104_01  세종특별자치시 연동면   080300
892       None          None    sk0118    sk0118_01  세종특별자치시 연동면   080300

[893 rows x 6 columns]

In [23]:
#딸기농가 아이디로 작기table 불러오기

df_id_list=list(raw_id['userId']) 
#df_id_list=['PFS_0000001','PFS_0000002','PFS_0000003']
url_crop= 'http://www.smartfarmkorea.net/Agree_WS/webservices/ProvideRestService/getCroppingSeasonDataList/fc918c3668964be490f67fe52bbef49c/'
list_df_cropping =[]
for i in df_id_list:
    # print(url_cropping)
    df_crop = pd.DataFrame(json.loads(requests.get(url_crop+i).text))
    df_crop['userId']=i
    list_df_cropping.append(df_crop)
df_cropping = pd.concat(list_df_cropping,ignore_index=True)
df_cropping

statusCode statusMessage croppingSerlNo croppingSeasonName  \
0            00   NORMAL_CODE           None               None   
1            00   NORMAL_CODE           None               None   
2            00   NORMAL_CODE           None               None   
3            00   NORMAL_CODE           None               None   
4            00   NORMAL_CODE           None               None   
...         ...           ...            ...                ...   
1812         00   NORMAL_CODE             10      마미리오_20160120   
1813         00   NORMAL_CODE             45       244_20160203   
1814         00   NORMAL_CODE            326           티티찰_2016   
1815       None          None            325            토마토_레드찰   
1816         00   NORMAL_CODE             47       244_20160202   

             croppingDate      croppingEndDate        croppingSystem itemCode  \
0                    None                 None                  None     None   
1                    None                 None                  None     None   
2                    None                 None                  None     None   
3                    None                 None                  None     None   
4                    None                 None                  None     None   
...                   ...                  ...                   ...      ...   
1812  2016-01-20 00:00:00  2016-12-31 00:00:00  B0004000000000000001   080300   
1813  2016-02-03 00:00:00  2016-12-31 00:00:00  B0004000000000000001   080300   
1814  2016-07-20 00:00:00  2016-12-31 00:00:00  B0004000000000000002   080300   
1815  2016-02-11 00:00:00  2016-12-31 00:00:00  B0004000000000000002   080300   
1816  2016-02-02 00:00:00  2016-12-31 00:00:00  B0004000000000000001   080300   

     cultivationArea calCultivationArea  ... planSlabNum plantDensity  \
0               None               None  ...        None         None   
1               None               None  ...        None         None   
2               None               None  ...        None         None   
3               None               None  ...        None         None   
4               None               None  ...        None         None   
...              ...                ...  ...         ...          ...   
1812          3000.0             9900.0  ...         5.0         2.73   
1813          3000.0             9900.0  ...         5.0         2.73   
1814             NaN               None  ...        None         None   
1815          1500.0               None  ...        None         None   
1816          3000.0             9900.0  ...         5.0         2.73   

     standardPlantDensity floodlightDec leafArea stndTemp stndWeight  \
0                    None          None     None     None       None   
1                    None          None     None     None       None   
2                    None          None     None     None       None   
3                    None          None     None     None       None   
4                    None          None     None     None       None   
...                   ...           ...      ...      ...        ...   
1812                  2.5           0.7      0.0     18.0      180.0   
1813                  2.5           0.7      0.0     18.0      180.0   
1814                 None           NaN     None      NaN       80.0   
1815                 None           0.7     None     18.0       80.0   
1816                  2.5           0.7      0.0     18.0      180.0   

     stndSolar stndMeta    userId  
0         None     None  LSDS_001  
1         None     None  LSDS_002  
2         None     None  LSDS_003  
3         None     None  LSDS_005  
4         None     None  LSDS_006  
...        ...      ...       ...  
1812     100.0    130.0    sk0085  
1813     100.0    130.0    sk0091  
1814       NaN     None    sk0104  
1815     100.0     None    sk0104  
1816     100.0    130.0    sk0118  

[1817 rows x 23 columns]

In [24]:
raw_id.to_excel(excel_writer='raw_id.xlsx')
df_cropping.to_excel(excel_writer='df_cropping.xlsx')

In [25]:
profile = ProfileReport(df_cropping, title="Report")
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

작기정보 set
- croppingSerlNo, 작기 번호가 없는 데이터 105개
- 